In [1]:
import geopandas as gpd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns 

In [2]:
# Caminho para o shapefile
shp_path = r"..\..\Data\Processed\PT-FireSprd_v3.0\L2_FireBehavior\PT-FireSprd_v3.0_L2_model.shp"

# 1. Ler o shapefile
gdf = gpd.read_file(shp_path)

# 4. Listar as variáveis restantes
print("\n=== Variáveis mantidas para análise ===")
print(gdf.columns.tolist())


=== Variáveis mantidas para análise ===
['ros_p', 'duration_p', 'elev_av', 'aspect_sin', 'aspect_cos', 'landform', 'land_use', '1_3y_fir_p', '3_8y_fir_p', '8_ny_fir_p', 'fuel_age', 'fuel_model', 'f_load_av', 'sW_1m_av', 'sW_3m_av', 'sW_7_av', 'sW_28_av', 'sW_100_av', 'sW_289_av', 't_2m_C_av', 'd_2m_C_av', 'rh_2m_av', 'VPD_Pa_av', 'sP_hPa_av', 'gp_m2s2_av', 'dfmc_av', 'HDW_av', 'Haines_av', 'FWI_12h_av', 'DC_12h_av', 'FFMC_12h_a', 'wv10_kh_av', 'wsin10_av', 'wcos10_av', 'wv100_k_av', 'wsin100_av', 'wcos100_av', 'Recirc', 'CircVar', 't_950_av', 't_850_av', 't_700_av', 't_500_av', 't_300_av', 'rh_950_av', 'rh_850_av', 'rh_700_av', 'rh_500_av', 'rh_300_av', 'wv_950_av', 'wv_850_av', 'wv_700_av', 'wv_500_av', 'wv_300_av', 'wsi_950_av', 'wco_950_av', 'wsi_850_av', 'wco_850_av', 'wsi_700_av', 'wco_700_av', 'wsi_500_av', 'wco_500_av', 'wsi_300_av', 'wco_300_av', 'vwv_950_av', 'vwv_850_av', 'vwv_700_av', 'vwv_500_av', 'vwv_300_av', 'gp_950_av', 'gp_850_av', 'gp_700_av', 'gp_500_av', 'gp_300_av

In [3]:
# 3. Selecionar apenas as variáveis numéricas
num_df = gdf.select_dtypes(include=["number"])

# 4. Calcular a matriz de correlação
corr_matrix = num_df.corr()


In [4]:
plt.figure(
    figsize=(
        max(10, len(corr_matrix.columns)),   # largura proporcional ao nº de variáveis
        max(10, 0.95 * len(corr_matrix.columns))    # altura menor para ficar mais "quadrado"
    )
)

ax = sns.heatmap(
    corr_matrix,
    cmap='coolwarm',
    center=0,
    annot=True,                 # ativa os valores nas células
    fmt=".2f",                  # formato (2 casas decimais)
    annot_kws={"size": 10},      # tamanho da fonte dos labels
    linewidths=0.3,
    cbar_kws={"shrink": 0.8}
)


plt.title(
    "Matriz de Correlação das Variáveis Ambientais e ROS",
    fontsize=136,   # título maior
    pad=140
)

cbar = ax.collections[0].colorbar
cbar.ax.tick_params(
    labelsize=72,    # tamanho da fonte
    length=30,       # comprimento dos ticks (aumenta o espaço visual)
    width=5,        # largura dos ticks
    direction='out'  # ou 'in' para ticks para dentro
)
# Rótulos maiores e mais legíveis
plt.xticks(rotation=90, fontsize=39)
plt.yticks(rotation=0, fontsize=39)

plt.tight_layout()
plt.savefig("..\..\Data\Data_Exploration\Correlation_Matrix.pdf", format="pdf", dpi=300, bbox_inches="tight")
plt.show()


In [5]:
import numpy as np
import pandas as pd

n = 200
pd.set_option("display.max_rows", n)  


# Criar matriz sem diagonal
corr_mod = corr_matrix.abs().where(~np.eye(len(corr_matrix), dtype=bool))

# Manter só metade superior da matriz (remove duplicados)
corr_upper = corr_mod.where(np.triu(np.ones(corr_mod.shape), k=1).astype(bool))

# Transformar em DataFrame limpo
df_corr = (
    corr_upper
    .stack()
    .sort_values(ascending=False)
    .reset_index()
)

df_corr.columns = ["Var1", "Var2", "Correlation"]

# Pegar somente top 50
top50 = df_corr.head(n)

print(top50)


           Var1        Var2  Correlation
0     Haines_av   gT_8_7_av     1.000000
1      sW_3m_av   sW_289_av     0.993808
2      sW_1m_av   sW_100_av     0.993450
3      rh_2m_av     dfmc_av     0.991380
4     sP_hPa_av  gp_m2s2_av     0.986714
5    wcos100_av  wco_950_av     0.976510
6    wsin100_av  wsi_950_av     0.976323
7     wsin10_av  wsin100_av     0.966919
8     wcos10_av  wcos100_av     0.966347
9    HigCC_p_av  TotCC_p_av     0.960621
10     rh_2m_av  LCL_hPa_av     0.952708
11    wcos10_av  wco_950_av     0.951818
12    wsin10_av  wsi_950_av     0.948166
13    t_2m_C_av   VPD_Pa_av     0.947392
14     sW_3m_av   sW_100_av     0.945940
15    gp_500_av   gp_300_av     0.944097
16     sW_1m_av    sW_28_av     0.943086
17      dfmc_av  LCL_hPa_av     0.936807
18       Recirc     CircVar     0.934363
19    wv_500_av    wSv_5_av     0.933892
20    wv_700_av    wSv_7_av     0.931622
21     sW_1m_av    sW_3m_av     0.930917
22    gp_700_av   gp_500_av     0.923691
23    gp_850_av 